In [1]:
from tensorflow.python.client import device_lib
print(device_lib.list_local_devices())

[name: "/device:CPU:0"
device_type: "CPU"
memory_limit: 268435456
locality {
}
incarnation: 4243375815785253064
xla_global_id: -1
, name: "/device:GPU:0"
device_type: "GPU"
memory_limit: 2254123828
locality {
  bus_id: 1
  links {
  }
}
incarnation: 16524026339886444757
physical_device_desc: "device: 0, name: GeForce GTX 1650 Ti, pci bus id: 0000:01:00.0, compute capability: 7.5"
xla_global_id: 416903419
]


In [2]:
# %run KcELECTRA-base.version.py
# !pip freeze

In [3]:
import re
import torch
import pandas as pd

# deivce 선택
device = torch.device('cuda:0' if torch.cuda.is_available() else 'cpu')
print("device:", device)

device: cpu


In [4]:
# 엑셀 파일에서 데이터프레임 읽기
df = pd.read_excel(r"C:\Users\GJAISCHOOL\Desktop\X_filter\Algorithm\dataset\sample_data(100).xlsx")

# 'Sentence' 칼럼의 값을 문자열로 변환하여 리스트로 저장
str_data = df['Sentence'].astype(str).tolist()

# 'Sentence' 칼럼의 값을 하나의 문자열로 결합
all_sentences = ' '.join(str_data)

print(df.shape)
df.head()

(100, 2)


Sentence  label
0                                    좌배 까는건 ㅇㅂ      1
1                 집에 롱 패딩만 세 개다. 10년 더 입어야지 ㅋㅋ      0
2  개소리야 니가 빨갱이를 옹호하고 드루킹을 ㅇㅇ짓이라고 말못해서 삐진거야 빨갱아      1
3                                  세탁이라고 봐도 된다      0
4                            애새끼가 초딩도 아니고 ㅋㅋㅋㅋ      1

In [5]:
null_idx = df[df.label.isnull()].index                             # 해당 index에 null 값 확인
df.loc[null_idx, "Sentence"]                                       # null 값이 존재한 인덱스의 content 값 불러오기

# lable은 content의 가장 끝 문장열로 설정
df.loc[null_idx, "label"] = df.loc[null_idx, "Sentence"].apply(lambda x: x[-1])

# content는 "\t" 앞부분까지의 문자열로 설정
df.loc[null_idx, "Sentence"] = df.loc[null_idx, "Sentence"].apply(lambda x: x[-2])

In [6]:
import sys
sys.path.append(r'C:\Users\GJAISCHOOL\Desktop\X_filter\Algorithm\Morphological_Analyzer')

In [7]:
from kiwipiepy import Kiwi
kiwi= Kiwi(num_workers=0, model_path=None, load_default_dict=True, integrate_allomorph=False)

kiwi_pre_train = df.sample(frac=0.8, random_state=42)                     # train(80%), test(20%) 셋 구분 
kiwi_pre_test = df.drop(kiwi_pre_train.index)                             # 랜덤으로 샘플링(랜덤으로 숫자 배치)

# 데이터셋 갯수 확인
print('중복 제거 전 학습 데이터셋 : {}'.format(len(kiwi_pre_train)))
print('중복 제거 전 테스트 데이터셋 : {}'.format(len(kiwi_pre_test)))

# 중복 데이터 제거
kiwi_pre_train.drop_duplicates(subset=["Sentence"], inplace=True)
kiwi_pre_test.drop_duplicates(subset=["Sentence"], inplace=True)

# 형태소 분석 적용
train_morp = list(kiwi.tokenize(kiwi_pre_train['Sentence'].tolist(), normalize_coda=True))
test_morp = list(kiwi.tokenize(kiwi_pre_test['Sentence'].tolist(), normalize_coda=True))

train_data = [train_morp, kiwi_pre_train['label']]
test_data = [test_morp, kiwi_pre_test['label']]


# 데이터셋 갯수 확인
print('중복 제거 후 학습 데이터셋 : {}'.format(len(train_data[0])))
print('중복 제거 후 테스트 데이터셋 : {}'.format(len(test_data[0])))


중복 제거 전 학습 데이터셋 : 80
중복 제거 전 테스트 데이터셋 : 20
중복 제거 후 학습 데이터셋 : 80
중복 제거 후 테스트 데이터셋 : 20


In [8]:
# 각 문장에서 최대 토큰 수 계산
train_max_tokens = max(len(sentence) for sentence in train_data[0])

# DataFrame 생성
train_df = pd.DataFrame(index=range(len(train_data[0])), columns=range(train_max_tokens + 1))

# 각 문장에 대해 반복하면서 DataFrame 생성
for i, sentence in enumerate(train_data[0]):
    # DataFrame에 토큰 형태 추가
    for j, token in enumerate(sentence):
        train_df.loc[i, j] = token.form

    # 마지막 열에 'label' 값 추가
    train_df.loc[i, train_max_tokens] = train_data[1].iloc[i]

# NaN 값을 빈 문자열로 대체
train_df = train_df.fillna('')

# 결과적인 DataFrame 출력
print(train_df)


    0     1   2    3   4    5    6   7    8    9    ... 119 120 121 122 123  \
0    새로     오   면    다  그렇    게    하   ᆷ  열심히    하  ...                       
1   오마쥬     가   뭐    이  ᆫ지    ᆫ    알   ᆷ    ?       ...                       
2     아    그런   거    이   야    ?  ㅋㅋㅋ                ...                       
3    용접    협회  무시    하   지    말   아라   .   저기   현장  ...                       
4    시발    정작   지    네   들   자식    은   몸    쓰    는  ...                       
..  ...   ...  ..  ...  ..  ...  ...  ..  ...  ...  ...  ..  ..  ..  ..  ..   
75  용팔이                                             ...                       
76   대구    경북  당선   조건   :  매국노                     ...                       
77   면도     뭐   ᆫ  스머프  모자    쓰    고   오    앗    네  ...                       
78   여자     들   물    뽕  처먹    여   강간   하    고  동영상  ...                       
79  그래서  씨발롬아  PC    가  나쁘   다는    거   이    야    좋  ...                       

   124 125 126 127 128  
0                    0  
1

In [9]:
# 각 문장에서 최대 토큰 수 계산
test_max_tokens = max(len(sentence) for sentence in test_data[0])
# DataFrame 생성
test_df = pd.DataFrame(index=range(len(test_data[0])), columns=range(test_max_tokens + 1))  # Add one more column for 'label'

# 각 문장에 대해 반복하면서 DataFrame 생성
for i, sentence in enumerate(test_data[0]):
    # DataFrame에 토큰 형태 추가
    for j, token in enumerate(sentence):
        test_df.loc[i, j] = token.form

    # 마지막 열에 'label' 값 추가
    test_df.loc[i, test_max_tokens] = test_data[1].iloc[i]  # Use .iloc[i] to access the value at index i

# NaN 값을 빈 문자열로 대체
test_df = test_df.fillna('')

# 결과적인 DataFrame 출력
print(test_df)


      0      1    2     3     4    5         6   7   8    9   ... 29  30  31  \
0      집      에    롱    패딩     만    세         개   이   다    .  ...              
1    개소리      야    니     가   빨갱이    를        옹호   하   고  드루킹  ...              
2    박근혜      안    빨    는데    보수   통합         3  원칙  인정    하  ...              
3      열     사발  들이키    어도    아깝    지         않   음           ...              
4   정신병자     천국    이    구나                                    ...              
5      나      ᆫ  사이트    마다   아이디    /        비번   다  다르    고  ...  이  엑셀  파일   
6     군대     에서   여군     이    필요    하        ᆫ가               ...              
7     호주     에서    는    남자     들    이        동물  보다  못하    ᆫ  ...              
8     꼴리      지    는     않     고   그냥        존나  귀엽   다       ...              
9     그냥    선거철    에     지   지지자   결집        시키   는   거    이  ...  이  니까       
10    미치      었    나    진짜    시발                              ...              
11    ㄹㅇ     시위   진압  ㅆㅅㅌㅊ     이    었   

In [10]:
from nltk.corpus import stopwords
from nltk.tokenize import word_tokenize
from konlpy.tag import Okt
import nltk

okt = Okt()

# 불용어(stopwords) 리스트를 직접 만들어 사용하거나, 외부에서 가져와 사용합니다.
stop_words = set(['는', '은', '이', '가', '을', '를'])  # 사용자 정의 불용어 리스트 예시

# 불용어(stopwords) 리스트에 사용자 정의 불용어를 추가합니다.
# stop_words = set(stopwords.words('english') + custom_stopwords)

for column_index in train_df.columns:
    for index, value in enumerate(train_df[column_index]):
        if isinstance(value, str):  # 문자열인 경우에만 토큰화 수행
            word_tokens = word_tokenize(value)
            # 불용어 제거
            train_df[column_index][index] = ' '.join([word for word in word_tokens if not word in stop_words])
            
        else:
            pass

train_df['merged_sentences'] = train_df.apply(lambda row: ' '.join([str(token) for token in row if token is not None]), axis=1)
print(train_df['merged_sentences'])


C:\Users\GJAISCHOOL\AppData\Local\Temp\ipykernel_1180\3556465901.py:19: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  train_df[column_index][index] = ' '.join([word for word in word_tokens if not word in stop_words])
C:\Users\GJAISCHOOL\AppData\Local\Temp\ipykernel_1180\3556465901.py:19: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  train_df[column_index][index] = ' '.join([word for word in word_tokens if not word in stop_words])
C:\Users\GJAISCHOOL\AppData\Local\Temp\ipykernel_1180\3556465901.py:19: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the docum

0     새로 오 면 다 그렇 게 하 ᆷ 열심히 하  티  팍팍 내 고 뭐 바꾸 고 뭐 하 ...
1     오마쥬  뭐  ᆫ지 ᆫ 알 ᆷ ?                            ...
2     아 그런 거  야 ? ㅋㅋㅋ                               ...
3     용접 협회 무시 하 지 말 아라 . 저기 현장 고수 및 용접 에 관하 ᆫ 전문 지식...
4     시발 정작 지 네 들 자식  몸 쓰  일 안 시키 ᆯ 거  면서 개지랄떠네 ㅋㅋㅋ ...
                            ...                        
75    용팔이                                           ...
76    대구 경북 당선 조건 : 매국노                             ...
77    면도 뭐 ᆫ 스머프 모자 쓰 고 오 앗 네                       ...
78    여자 들 물 뽕 처먹 여 강간 하 고 동영상 찍  것  죄  아니 었 구나 ㅋㅋ 버...
79    그래서 씨발롬아 PC  나쁘 다는 거  야 좋 다는 거  야 ?           ...
Name: merged_sentences, Length: 80, dtype: object


C:\Users\GJAISCHOOL\AppData\Local\Temp\ipykernel_1180\3556465901.py:19: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  train_df[column_index][index] = ' '.join([word for word in word_tokens if not word in stop_words])
C:\Users\GJAISCHOOL\AppData\Local\Temp\ipykernel_1180\3556465901.py:19: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  train_df[column_index][index] = ' '.join([word for word in word_tokens if not word in stop_words])
C:\Users\GJAISCHOOL\AppData\Local\Temp\ipykernel_1180\3556465901.py:19: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the docum

In [11]:
for column_index in test_df.columns:
    for index, value in enumerate(test_df[column_index]):
        if isinstance(value, str):  # 문자열인 경우에만 토큰화 수행
            word_tokens = word_tokenize(value)
            # 불용어 제거
            test_df[column_index][index] = ' '.join([word for word in word_tokens if not word in stop_words])
            
        else:
            pass

test_df['merged_sentences'] = test_df.apply(lambda row: ' '.join([str(token) for token in row if token is not None]), axis=1)
print(test_df['merged_sentences'])

0     집 에 롱 패딩 만 세 개  다 . 10 년 더 입 어야지 ㅋㅋ           ...
1     개소리 야 니  빨갱이  옹호 하 고 드루킹  ㅇㅇ 짓  라고 말 못 하 여서 삐지...
2     박근혜 안 빨 는데 보수 통합 3 원칙 인정 하 ᆷ                  ...
3     열 사발 들이키 어도 아깝 지 않 음                          ...
4       정신병자 천국  구나                                   1
5     나 ᆫ 사이트 마다 아이디 / 비번 다 다르 고 난이도 높 음 엑셀 파일 에 모든 ...
6     군대 에서 여군  필요 하 ᆫ가                             ...
7     호주 에서  남자 들  동물 보다 못하 ᆫ 존재  라던데 ㅋㅋ            ...
8     꼴리 지  않 고 그냥 존나 귀엽 다                          ...
9     그냥 선거철 에 지 지지자 결집 시키  거  ᆷ 자기 지지 층 에 ᆫ 아시아인  별...
10      미치 었 나 진짜 시발                                  1
11    ㄹㅇ 시위 진압 ㅆㅅㅌㅊ  었 음                            ...
12    영혼 까지 팔 아도 되 ᆫ다는 놈  ᆯ 거  야                    ...
13    진주  네요 ... 여기 동네 에 잠시 살 았 는데 ... 여기 주차 장난 아니 ᆸ...
14         나 안동 김 씨                                   0
15    ㅂㄷㅂㄷ ㅋㅋㅋㅋㅋ 중국 욕하니 ㅂㄷㅂㄷ 하죠 ㅋㅋㅋㅋㅋㅋㅋㅋ            ...
16       오이 오이 아부  네                                  0
17    무게 치  거 에 인생 버리 ᆫ 새끼 들                    

C:\Users\GJAISCHOOL\AppData\Local\Temp\ipykernel_1180\2334454352.py:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  test_df[column_index][index] = ' '.join([word for word in word_tokens if not word in stop_words])
C:\Users\GJAISCHOOL\AppData\Local\Temp\ipykernel_1180\2334454352.py:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  test_df[column_index][index] = ' '.join([word for word in word_tokens if not word in stop_words])
C:\Users\GJAISCHOOL\AppData\Local\Temp\ipykernel_1180\2334454352.py:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentat

In [12]:
from transformers import ElectraTokenizer, ElectraForSequenceClassification, TFElectraForSequenceClassification
from transformers import AutoTokenizer, AutoModelForSequenceClassification, TrainingArguments, Trainer
import torch

# KcELECTRA 모델 및 토크나이저 로드
model_name = "beomi/KcELECTRA-base"
tokenizer = AutoTokenizer.from_pretrained(model_name)

c:\Users\GJAISCHOOL\.conda\envs\nv38\lib\site-packages\tqdm\auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [13]:
tokenized_train_sentences = tokenizer(
    list(train_df['merged_sentences']),
    return_tensors="pt",
    max_length=128,
    padding=True,
    truncation=True,
    add_special_tokens=True
)

In [14]:
tokenized_test_sentences = tokenizer(
    list(test_df['merged_sentences']),
    return_tensors="pt",
    max_length=128,
    padding=True,
    truncation=True,
    add_special_tokens=True
)

In [15]:
print(tokenized_train_sentences[0])        # 0번째 문장에 해당하는 객체 
print(tokenized_train_sentences[0].tokens) # 0번째 문장에 토큰의 목록
print(tokenized_train_sentences[0].ids)    # 0번째 문장에 대한 고유 ID

Encoding(num_tokens=128, attributes=[ids, type_ids, tokens, offsets, attention_mask, special_tokens_mask, overflowing])
['ĠìĥĪë¡ľ', 'Ġìĺ¤', 'Ġë©´', 'Ġëĭ¤', 'Ġê·¸ëłĩ', 'Ġê²Į', 'Ġíķĺ', 'Ġ', 'áĨ', '·', 'ĠìĹ´ìĭ¬íŀĪ', 'Ġíķĺ', 'Ġ', 'Ġíĭ°', 'Ġ', 'ĠíĮįíĮį', 'ĠëĤ´', 'Ġê³ł', 'ĠëŃĲ', 'Ġë°Ķê¾¸', 'Ġê³ł', 'ĠëŃĲ', 'Ġíķĺ', 'Ġê¸°', 'Ġë¡ľ', 'Ġíķĺ', 'ĠìŀĲ', 'Ġìķķë°ķ', 'Ġ', 'Ġì£¼', 'Ġì§Ģ', 'ĠìķĬ', 'ĠëĥĲ', 'Ġ10', 'ĠëħĦ', 'Ġê°Ħ', 'ĠëĦĪë¬´', 'ĠíĥĢ', 'ìĦ±', 'ĠìĹĲ', 'Ġìłĸ', 'Ġìĸ´', 'ĠìĤ´', 'Ġìķ', 'ĺ', 'Ġëįĺ', 'Ġê±°', 'ĠìķĦëĭĪ', 'ĠëĥĲ', 'Ġ?', 'ĠìľĦê¸°', 'ê°Ĳ', 'ĠìĹĨìĿ´', 'Ġ', 'Ġ', 'Ġ', 'Ġ', 'Ġ', 'Ġ', 'Ġ', 'Ġ', 'Ġ', 'Ġ', 'Ġ', 'Ġ', 'Ġ', 'Ġ', 'Ġ', 'Ġ', 'Ġ', 'Ġ', 'Ġ', 'Ġ', 'Ġ', 'Ġ', 'Ġ', 'Ġ', 'Ġ', 'Ġ', 'Ġ', 'Ġ', 'Ġ', 'Ġ', 'Ġ', 'Ġ', 'Ġ', 'Ġ', 'Ġ', 'Ġ', 'Ġ', 'Ġ', 'Ġ', 'Ġ', 'Ġ', 'Ġ', 'Ġ', 'Ġ', 'Ġ', 'Ġ', 'Ġ', 'Ġ', 'Ġ', 'Ġ', 'Ġ', 'Ġ', 'Ġ', 'Ġ', 'Ġ', 'Ġ', 'Ġ', 'Ġ', 'Ġ', 'Ġ', 'Ġ', 'Ġ', 'Ġ', 'Ġ', 'Ġ', 'Ġ', 'Ġ', 'Ġ', 'Ġ', 'Ġ', 'Ġ', 'Ġ', 'Ġ', 'Ġ', 'Ġ']
[3718, 578, 2172, 374, 1639, 1337, 313, 188, 1187, 118, 2348, 313, 188, 2

In [16]:
class CurseDataset(torch.utils.data.Dataset):
    def __init__(self, encoding, labels):
        self.encodings = encoding
        self.labels = labels
    
    def __getitem__(self, idx):
        item = {key: torch.tensor(val[idx]) for key, val in self.encodings.items()} # self.encodings 딕셔너리 내의 값 중에 val를 torch.tensor로 변환해 하여
        item["labels"] = torch.tensor(self.labels[idx])                             # key: toch.tensor(val[ix])라는 item 딕셔너리 형성
        return item                                                                 # 새로운 labels 키 값에 value torch.tensor(self.labels[idx]) 쌍을 생성
    
    def __len__(self):
        return len(self.labels)                                                     # self.labels 길이 반환

In [18]:
# train_set, test_set에 대한 데이터셋을 각각 생성

train_label = train_df[128].values
test_label = test_df[38].values

train_dataset = CurseDataset(tokenized_train_sentences, train_label)
test_dataset = CurseDataset(tokenized_test_sentences, test_label)


In [19]:
model = AutoModelForSequenceClassification.from_pretrained(model_name, num_labels=2)   # 사전 학습된 모델 찾아오기
model.to(device)

Some weights of the model checkpoint at beomi/KcELECTRA-base were not used when initializing ElectraForSequenceClassification: ['discriminator_predictions.dense.bias', 'discriminator_predictions.dense.weight', 'discriminator_predictions.dense_prediction.weight', 'discriminator_predictions.dense_prediction.bias']
- This IS expected if you are initializing ElectraForSequenceClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing ElectraForSequenceClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of ElectraForSequenceClassification were not initialized from the model checkpoint at beomi/KcELECTRA-base and are newly initialized: ['classifier.dense.bias', 'classifier.ou

ElectraForSequenceClassification(
  (electra): ElectraModel(
    (embeddings): ElectraEmbeddings(
      (word_embeddings): Embedding(30000, 768, padding_idx=3)
      (position_embeddings): Embedding(512, 768)
      (token_type_embeddings): Embedding(2, 768)
      (LayerNorm): LayerNorm((768,), eps=1e-12, elementwise_affine=True)
      (dropout): Dropout(p=0.1, inplace=False)
    )
    (encoder): ElectraEncoder(
      (layer): ModuleList(
        (0-11): 12 x ElectraLayer(
          (attention): ElectraAttention(
            (self): ElectraSelfAttention(
              (query): Linear(in_features=768, out_features=768, bias=True)
              (key): Linear(in_features=768, out_features=768, bias=True)
              (value): Linear(in_features=768, out_features=768, bias=True)
              (dropout): Dropout(p=0.1, inplace=False)
            )
            (output): ElectraSelfOutput(
              (dense): Linear(in_features=768, out_features=768, bias=True)
              (LayerNorm): L

In [20]:
# 3 - 2 학습 파라미터 설정
training_args = TrainingArguments(
    output_dir = './results',           # 학습결과 저장경로
    num_train_epochs=10,                # 학습 epoch 설정
    per_device_train_batch_size = 8,    # train batch_size 설정
    per_device_eval_batch_size = 64,    # test batch_size 설정
    logging_dir = './logs',             # 학습 log 저장경로
    logging_steps=500,                  # 학습 log 기록 단위
    save_total_limit = 2,               # 학습결과 저장 최대갯수
)

In [21]:
from sklearn.metrics import precision_recall_fscore_support, accuracy_score

# 학습과정에서 사용할 평가지표를 위한 함수 설정
def compute_metrics(pred):
  labels = pred.label_ids
  preds = pred.predictions.argmax(-1)
  # 정밀도, 재현율, f1 구하기 
  precision, recall, f1, _ = precision_recall_fscore_support(labels, preds, average='binary')
  # 정확도 구하기
  acc = accuracy_score(labels, preds)
  return{
      'accuracy': acc,
      'f1': f1,
      'precision': precision,
      'recall': recall
  }

In [22]:
# Trainer 모듈을 사용해 모델의 학습을 컨트롤하은 trainer를 생성
trainer = Trainer(
    model = model,                       # 학습하고자하는 Transformers model
    args=training_args,                  # 위에서 정의한 Trainging Arguments
    train_dataset=train_dataset,         # 학습 데이터셋
    eval_dataset=test_dataset,           # 평가 데이터셋
    compute_metrics=compute_metrics,     # 평가지표
)

In [23]:
type(trainer)

transformers.trainer.Trainer

In [24]:
trainer.train()

c:\Users\GJAISCHOOL\.conda\envs\nv38\lib\site-packages\transformers\optimization.py:411: FutureWarning: This implementation of AdamW is deprecated and will be removed in a future version. Use the PyTorch implementation torch.optim.AdamW instead, or set `no_deprecation_warning=True` to disable this warning
  warnings.warn(
  0%|          | 0/100 [00:00<?, ?it/s]C:\Users\GJAISCHOOL\AppData\Local\Temp\ipykernel_1180\1167134061.py:7: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
  item = {key: torch.tensor(val[idx]) for key, val in self.encodings.items()} # self.encodings 딕셔너리 내의 값 중에 val를 torch.tensor로 변환해 하여


In [ ]:
# 평가를 수행하고 custom_ 접두사가 붙은 평가 지표를 출력
results = trainer.evaluate(eval_dataset=test_dataset, metric_key_prefix='custom_')

print(results)

In [ ]:
def kiwi(sentence):
    word_tokens = word_tokenize(sentence)
    result = []
    for word in word_tokens: 
        if word not in stop_words: 
            result.append(word)
    # 리스트의 요소를 공백으로 구분된 하나의 문자열로 결합
    result_string = ' '.join(result)
    return result_string

In [ ]:
# 0: curse, 1: non_curse
def sentence_predict(sent):
    # 평가모드로 변경
    model.eval()

    # 입력된 문장 토크나이징
    tokenized_sent = tokenizer(
        kiwi(sent),
        return_tensors="pt",
        truncation=True,
        add_special_tokens=True,
        max_length=128
    )

    # 모델이 위치한 GPU로 이동
    # tokenized_sent.to(deivce)

    # 예측
    with torch.no_grad():
        outputs = model(
            input_ids=tokenized_sent["input_ids"],
            attention_mask=tokenized_sent["attention_mask"],
            token_type_ids=tokenized_sent["token_type_ids"]
        )

    # 결과 return
    logits = outputs[0]
    logits = logits.detach().cpu()
    result = logits.argmax(-1)
    sentence = True
    input_sentence = tokenized_sent["input_ids"]
    if result == 0:
        sentence = True

    elif result == 1:
        sentence = False
    return sentence, input_sentence


sentence_predict("씨발이게 맞아?")

In [ ]:
def found_word(input_sentence, found_bad_word):
    result = input_sentence
    if found_bad_word:
        result = badword_find(result)
    return result

def badword_find(input_sentence):
    result = input_sentence
    badword_df = pd.read_excel(r'C:\Users\GJAISCHOOL\Desktop\X_filter\Algorithm\dataset\word_list.xlsx')
    
    found_bad_word = False  # 입력 문장에 단어가 발견되었는지를 나타내는 플래그
    for idx, row in badword_df.iterrows():
        if row["WORD"] in input_sentence:
            # 'WORD'가 입력 문장에 포함된 경우
            new_word = row["대체어"]
            if not pd.isnull(new_word):
                result = result.replace(row["WORD"], new_word)
                found_bad_word = True
            else:
                result = result.replace(row["WORD"], "*" * len(row["WORD"]))
                found_bad_word = True
    
    if not found_bad_word:
        # result = "@" * len(input_sentence)
        result = "혐오 표현입니다."
    return result

# 테스트
input_sentence = "엄마가 죽었으면 좋겠어"
speak_result = badword_find(input_sentence)
print(speak_result)

In [ ]:
badword_find(input_sentence)

In [ ]:
def speak(sent):
    sentence = sentence_predict(sent)
    if sentence[0] == False:
        return sent
    elif sentence[0] == True:
        return badword_find(sent)

In [ ]:
import kss
from pykospacing import Spacing
from soynlp.normalizer import repeat_normalize

# 띄어쓰기 설정
spacing = Spacing()

In [ ]:
# 특수문자 제거
def cleanse(text):
    pattern = re.compile(r'\s+')
    text = re.sub(pattern, ' ', text)
    text = re.sub('[^가-힣ㄱ-ㅎㅏ|a-zA-Z0-9]','', text)
    return text

In [ ]:
def clean_and_repeat_normalize(text):
    cleansed_text = cleanse(text)                                             # 특수문자 제거
    normalized_text = repeat_normalize(cleansed_text, num_repeats=2)          # 중복문자 제거
    input_data = re.sub(r'\d', '', normalized_text)                           # 숫자 제거
    normalized_text = spacing(input_data)                                     # 띄어쓰기 보정 

    return normalized_text

clean_and_repeat_normalize("아버지가방에들어가신다")

In [ ]:
def final_output():
    input_text = clean_and_repeat_normalize(input())
    sentences = kss.split_sentences(input_text)

    sentences_list = []
    for sentence in sentences:
        text_output = speak(sentence)
        sentences_list.append(text_output)

    long_test = ' '.join(sentences_list)
    print(long_test)
    return long_test

In [ ]:
final_output()
